In [65]:
import plotly.express as px
import pandas as pd
import plotly.graph_objects as go
from tabulate import tabulate

num_runs = 1000
columns1=['date', 'farm_count', 'exposed', 'infected', 'deceased', 'num_run']
columns2=['date', 'contact_type', 'num_inf_pigs', 'num_run']

# Import data from file
results_all_long = pd.read_csv('../output/results_by_compart_all.txt', sep=',', names=columns1)
results_by_contact_long = pd.read_csv('../output/results_by_contact_grp_all.txt', sep=',', names=columns2)
print(results_all_long)

# Find the indicies of the max infected farm count for each simulation run
max_farm_count_idx = results_all_long.groupby(['num_run'])['farm_count'].transform(max) == results_all_long['farm_count']
max_farm_count_dup = results_all_long[max_farm_count_idx]

print(results_all_long[max_farm_count_idx])

# To choose the first date that it occured since there are duplicates
max_farm_count_min_date_idx = max_farm_count_dup.groupby(['num_run'])['date'].transform(min) == max_farm_count_dup['date']
max_farm_count = max_farm_count_dup[max_farm_count_min_date_idx]
print(max_farm_count)


             date  farm_count  exposed  infected  deceased  num_run
0      2014-01-01           1        0         1         0     1000
1      2014-01-02           2        4         1         0     1000
2      2014-01-03           2       11         4         0     1000
3      2014-01-04           3       26        10         0     1000
4      2014-01-05           3       60        20         1     1000
...           ...         ...      ...       ...       ...      ...
88995  2014-03-26           1        0         0         0        9
88996  2014-03-27           1        0         0         0        9
88997  2014-03-28           1        0         0         0        9
88998  2014-03-29           1        0         0         0        9
88999  2014-03-30           1        0         0         0        9

[89000 rows x 6 columns]


In [76]:
index_farm_file = '../output/index_cases.txt'

index_farm = []  # type: List[str]

with open(index_farm_file, 'r') as f:
    for line in f:
        while line != "": # To stop when the end of file is reached

            # Ignore first line of each set
            run_line = f.readline()
            # Read in run line and store simulation run number
            run_info = run_line.split(" ")
            run_num = run_info[1].rstrip("\n")

            # Skip to next line
            farm_line = f.readline()
            # Store description line for output file
            line_info = farm_line.split('[')
            farm_info = line_info[1].rstrip("\n")
            farm_info = farm_info.strip(']')
            index_farm_info = farm_info.split(", ")
            index_farm_info.append(run_num)

            index_farm.append(index_farm_info)
            # Read next 2 lines
            line = f.readline()
            line = f.readline()

In [75]:
index_farm_df = pd.DataFrame (index_farm, columns = ['tvd_nr', 'year',
                                                     'farm_type', 'gde_nr', 'gde_name',
                                                     'pig_stall','tot_pigs', 'other_animals',
                                                     'which_animals', 'num_run'])


In [85]:
max_farm_count_df = pd.DataFrame(max_farm_count)
max_farm_count['num_run'] = max_farm_count['num_run'].astype(int)
index_farm_df['num_run'] = index_farm_df['num_run'].astype(int)
index_farm_df['tot_pigs'] = index_farm_df['tot_pigs'].astype(float).astype(int)
max_inf_count_merge = pd.merge(index_farm_df, max_farm_count, on='num_run')
print(max_inf_count_merge)

      tvd_nr  year           farm_type  gde_nr               gde_name  \
0    1829488  2014         'Fattening'  5484.0              'Gollion'   
1    1593884  2014             'Mixed'  1093.0           'Neuenkirch'   
2    1593501  2014         'Fattening'  1093.0           'Neuenkirch'   
3    1998719  2014           'Weaning'  5404.0           'Corbeyrier'   
4    1157567  2014         'Fattening'  1362.0                 'Arth'   
..       ...   ...                 ...     ...                    ...   
995  1398632  2014         'Fattening'   605.0                'Bowil'   
996  1291292  2014             'Mixed'  6437.0  'Les Ponts-de-Martel'   
997  1140101  2014         'Fattening'  3312.0          'Benken (SG)'   
998  1513677  2014         'Fattening'  2302.0           'St. Antoni'   
999  1196474  2014  'AllYearHusbandry'     nan                    nan   

    pig_stall  tot_pigs other_animals     which_animals  num_run        date  \
0       'Yes'       124          'No'      

C:\Users\km21a901\AppData\Local\Temp/ipykernel_11844/4214018751.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [206]:
fig_max_farm4 = px.scatter(max_inf_count_merge,
                             x='date',
                           y='farm_count',
                            template="plotly_white",
                           color='farm_type',
                           size='tot_pigs',
                           marginal_x="histogram",
                           marginal_y="histogram",
                           labels={'x':'Date', 'y':'Maximum Number of Infected Farms'},
                           title="Maximum Number of Infected Farms by Earliest Date for Each Simulation")

fig_max_farm4.show()

In [216]:
index_farm_sim_data = pd.merge(index_farm_df, results_all_long, on='num_run')
print(index_farm_sim_data)

        tvd_nr  year           farm_type  gde_nr   gde_name pig_stall  \
0      1829488  2014         'Fattening'  5484.0  'Gollion'     'Yes'   
1      1829488  2014         'Fattening'  5484.0  'Gollion'     'Yes'   
2      1829488  2014         'Fattening'  5484.0  'Gollion'     'Yes'   
3      1829488  2014         'Fattening'  5484.0  'Gollion'     'Yes'   
4      1829488  2014         'Fattening'  5484.0  'Gollion'     'Yes'   
...        ...   ...                 ...     ...        ...       ...   
88995  1196474  2014  'AllYearHusbandry'     nan        nan       nan   
88996  1196474  2014  'AllYearHusbandry'     nan        nan       nan   
88997  1196474  2014  'AllYearHusbandry'     nan        nan       nan   
88998  1196474  2014  'AllYearHusbandry'     nan        nan       nan   
88999  1196474  2014  'AllYearHusbandry'     nan        nan       nan   

       tot_pigs other_animals which_animals  num_run        date  farm_count  \
0           124          'No'           nan

In [215]:
fig_max_farm5 = px.line(index_farm_sim_data, x="date", y="farm_count",
                        facet_col="farm_type",
                        color="num_run",
                        facet_col_wrap=3,
                        title='Daily Number of Infected Farms by Index Case Farm Type',
                        template="plotly_white",
                        labels={'x':'Date', 'y':'Number of Infected Farms'},)
fig_max_farm5.show()

In [ ]:
# TODO Incomplete
# Looking at gemeinde of index case
fig_contact_type3 = px.pie(max_inf_count_merge, values='num_inf_pigs', names='contact_type',
             title='Percent of Infected Pigs by Contact Type')
fig_contact_type3.show()
fig_contact_type3.write_image('../output/' + str(num_runs) + '_num_inf_pig_by_contact_type_pie.png')

In [155]:
#from tabulate import tabulate
# Number of farms
#Summarize farm_type
farm_type_grp = pd.DataFrame(max_inf_count_merge.groupby('farm_type').size().reset_index(name='total'))

#print(tabulate(farm_type_grp, headers=['farm_type', 'total'],tablefmt='pretty'))

                farm_type  total
0      'AllYearHusbandry'    155
1              'Breeding'     29
2  'CoOperationHusbandry'      4
3   'EnterpriseHusbandry'     15
4             'Fattening'    515
5                 'Mixed'    198
6   'ProductionHusbandry'      6
7    'SummeringHusbandry'     61
8               'Unknown'      2
9               'Weaning'     15


In [164]:
# Set CSS properties for th elements in dataframe
th_props = [
  ('font-size', '11px'),
  ('text-align', 'center'),
  ('font-weight', 'bold'),
  ('color', 'white'),
  ('background-color', '#315399')
  ]

# Set CSS properties for td elements in dataframe
td_props = [
  ('font-size', '11px')
  ]

# Set table styles
styles = [
  dict(selector="th", props=th_props),
  dict(selector="td", props=td_props)
  ]


# Get rid of index column and render table as formatted
farm_type_grp.style.format().hide_index().set_table_styles(styles)

In [166]:
# Import data from file
agis_data_summ = pd.read_csv('../data/agis_data_lim.csv', header=0, encoding='latin-1')

In [172]:
# determine the number of holding types in 2014
farm_type_grp = pd.DataFrame(agis_data_summ.groupby(['holding_cat', 'year']).size().reset_index(name='count'))
farm_type_grp_2014 = farm_type_grp[farm_type_grp['year'] == 2014]

In [198]:
# Add a total row at the bottom of the table
farm_type_grp_2014_pt = farm_type_grp_2014.pivot_table(index=['holding_cat', 'year'],
               margins=True,
               margins_name='total',  # defaults to 'All'
               aggfunc=sum)
# Print styled table
farm_type_grp_2014_pt.style.format().set_table_styles(styles)

In [219]:
# Determine total number of pigs
farm_size_grp = pd.DataFrame(agis_data_summ.groupby(['holding_cat', 'year'], as_index=False).agg({
        'tot_pigs': sum
    }))
print(farm_size_grp)
farm_size_grp['tot_pigs'] = farm_size_grp['tot_pigs'].astype(int)
farm_size_grp_2014 = farm_size_grp[farm_size_grp['year'] == 2014]
# Add a total row at the bottom of the table
farm_size_grp_2014_pt = farm_size_grp_2014.pivot_table(index=['holding_cat', 'year'],
               margins=True,
               margins_name='total',  # defaults to 'All'
               aggfunc=sum)
# Print styled table

farm_size_grp_2014_pt.style.format().set_table_styles(styles)
# Determine total number of transports

          holding_cat  year  tot_pigs
0    AllYearHusbandry  2014   45016.0
1    AllYearHusbandry  2015   35312.0
2    AllYearHusbandry  2016   29547.0
3    AllYearHusbandry  2017   24350.0
4    AllYearHusbandry  2018   22974.0
..                ...   ...       ...
97            Weaning  2015    9915.0
98            Weaning  2016   11629.0
99            Weaning  2017   11143.0
100           Weaning  2018    8716.0
101           Weaning  2019    8068.0

[102 rows x 3 columns]


In [ ]:
# ugly...
import df2img

fig = df2img.plot_dataframe(
    farm_type_grp_2014_pt,
    title=dict(
        font_color="darkred",
        font_family="Times New Roman",
        font_size=16,
        text="AGIS Data for 2014",
    ),
    tbl_header=dict(
        align="right",
        fill_color="#315399",
        font_color="white",
        font_size=10,
        line_color="darkslategray",
    ),
    tbl_cells=dict(
        align="right",
        line_color="darkslategray",
    ),
    row_fill_color=("#ffffff", "#d7d8d6"),
    fig_size=(300, 500),
)

df2img.save_dataframe(fig=fig, filename="../output/df2img_table.png")

In [ ]:
# Not working...

import dataframe_image as dfi

dfi.export(farm_type_grp_2014_pt, 'dfi_table.png',
           table_conversion = 'matplotlib')

In [222]:
farm_type_grp_2014_pt.to_latex()

'\\begin{tabular}{llr}\n\\toprule\n      &      &  count \\\\\nholding\\_cat & year &        \\\\\n\\midrule\nAllYearHusbandry & 2014 &   1762 \\\\\nBreeding & 2014 &    351 \\\\\nCoOperationHusbandry & 2014 &     22 \\\\\nCoOperationPastureHusbandry & 2014 &      1 \\\\\nEnterpriseHusbandry & 2014 &    178 \\\\\nFattening & 2014 &   5694 \\\\\nLiveStockDealerEnterprise & 2014 &     16 \\\\\nMarketAuctionExhibition & 2014 &      4 \\\\\nMedicalCenter & 2014 &      2 \\\\\nMixed & 2014 &   2648 \\\\\nNonComercial & 2014 &    232 \\\\\nPopulation & 2014 &      6 \\\\\nProductionHusbandry & 2014 &     88 \\\\\nSlaughterEnterprise & 2014 &    473 \\\\\nSummeringHusbandry & 2014 &    641 \\\\\nUnknown & 2014 &     10 \\\\\nWeaning & 2014 &    137 \\\\\ntotal &      &  12265 \\\\\n\\bottomrule\n\\end{tabular}\n'

In [5]:
import datetime

num_runs = 1000
start_date = datetime.date.fromisoformat('2019-07-01')

import pandas as pd
output_dir = "../output/stochastic/" + str(start_date.year) + "_" + str(start_date.month) + "_" + str(start_date.day) + "/"
columns3 = ['tvd_nr', 'year', 'farm_type', 'gde_nr', 'gde_name',
                                                  'pig_stall', 'tot_pigs', 'other_animals', 'which_animals', 'num_run']

index_farm_df = pd.read_csv(output_dir + 'index_case_all.txt', sep=',', names=columns3)

In [8]:
columns1 = ['date', 'farm_count', 'exposed', 'infected', 'deceased', 'num_run']

results_all_long = pd.read_csv(output_dir + 'results_by_compart_all.txt', sep=',', names=columns1)

# Find the indicies of the max infected farm count for each simulation run
max_farm_count_idx = results_all_long.groupby(['num_run'])['farm_count'].transform(max) == results_all_long[
    'farm_count']
max_farm_count_dup = results_all_long[max_farm_count_idx]

print(results_all_long[max_farm_count_idx])

# To choose the first date that it occured since there are duplicates
max_farm_count_min_date_idx = max_farm_count_dup.groupby(['num_run'])['date'].transform(min) == max_farm_count_dup[
    'date']
max_farm_count = max_farm_count_dup[max_farm_count_min_date_idx]
print(max_farm_count)

             date  farm_count  exposed  infected  deceased  num_run
0      2019-07-01           1        0         1         0     1000
1      2019-07-02           1        3         1         0     1000
2      2019-07-03           1        7         1         1     1000
3      2019-07-04           1        5         2         2     1000
4      2019-07-05           1        6         3         2     1000
...           ...         ...      ...       ...       ...      ...
90895  2019-09-30           1        0         0         1      999
90987  2019-09-30        7118    33873    125677   1442659       99
91077  2019-09-28          45        0        18      1248        9
91078  2019-09-29          45        2        13      1253        9
91079  2019-09-30          45        2        12      1254        9

[16876 rows x 6 columns]
             date  farm_count  exposed  infected  deceased  num_run
0      2019-07-01           1        0         1         0     1000
183    2019-09-30     

In [17]:
print(index_farm_df)
print(index_farm_df.loc[index_farm_df['farm_type']=='Fattening   '])

      tvd_nr  year            farm_type   gde_nr       gde_name pig_stall  \
0    1492828  2019            Fattening   2338.0    La Verrerie       Yes   
1    2078953  2019   SummeringHusbandry      nan            nan       nan   
2    1735963  2019            Fattening   5607.0        Puidoux       Yes   
3    1124866  2019     AllYearHusbandry      nan            nan       nan   
4    1046359  2019            Fattening   1630.0    Glarus Nord       Yes   
..       ...   ...                  ...      ...            ...       ...   
995  1569308  2019                Mixed   1008.0     Schüpfheim       Yes   
996  1371055  2019            Fattening    324.0     Bleienbach       Yes   
997  1452815  2019     AllYearHusbandry      nan            nan       nan   
998  1603552  2019                Mixed   1125.0   Dagmersellen       Yes   
999  2082905  2019   SummeringHusbandry      nan            nan       nan   

     tot_pigs other_animals    which_animals  num_run  
0        44.0      